In [2]:
from additive_util import *

In [3]:
pd.options.display.max_rows = 50
pd.set_option('display.max_columns', None)

## Utility Functions

In [4]:
def parse_toolpath_dict(FolderName,FileName,dt):
    toolpath, state, endTime = parse_toolpath(FolderName,FileName,dt)
    toolpath_tuple = [tuple(l) for l in toolpath]
    return dict(zip(toolpath_tuple,state)), endTime

def parse_toolpath(FolderName,FileName,dt):
    """
    Extracts the information about the toolpath
    """
    complete_filename = os.path.join(FolderName,FileName)
    toolpath_raw=pd.read_csv(complete_filename,delimiter=r"\s+",header=None, \
                names=['time','x','y','z','state'])
    toolpath=[]
    state=[]
    time=0.0
    ind=0
    endTime = float(toolpath_raw.tail(1)['time'])
    while(time<=endTime):
        while(time>=toolpath_raw['time'][ind+1]):
            ind=ind+1
        X=toolpath_raw['x'][ind]+(toolpath_raw['x'][ind+1]-toolpath_raw['x'][ind])*(
            time-toolpath_raw['time'][ind])/(toolpath_raw['time'][ind+1]-toolpath_raw['time'][ind])
        Y=toolpath_raw['y'][ind]+(toolpath_raw['y'][ind+1]-toolpath_raw['y'][ind])*(
            time-toolpath_raw['time'][ind])/(toolpath_raw['time'][ind+1]-toolpath_raw['time'][ind])
        Z=toolpath_raw['z'][ind]+(toolpath_raw['z'][ind+1]-toolpath_raw['z'][ind])*(
            time-toolpath_raw['time'][ind])/(toolpath_raw['time'][ind+1]-toolpath_raw['time'][ind])
        toolpath.append([X,Y,Z])
        state.append(toolpath_raw['state'][ind+1])
        time = time +dt
    return toolpath, state, endTime

def getTemperature(p, indices, timestep, dataframe):
    """
    Extracts the temperature of a point
    - If it does not exist, it is set to a default temperature
    """
    xyzTuple = p.getXYZ()
    
    if xyzTuple in indices.keys() and timestep>0:
        dfIndex = indices[xyzTuple]
        series = dataframe.iloc[dfIndex]
        temp_timestep = series[timestep+4]
        return temp_timestep
    else:
        return NON_EXISTING_TEMP
    
def findNeighborTemperatures(p, indices, timestep,dataframe):
    """
    Extracts the temperature of neighboring voxels
    - Timestep is considered as 1 by default
    """
    neighbors = []

    ### immediate/adjacent neighbors - 1 degree
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y, p.Z),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y, p.Z),indices, timestep, dataframe)]

    neighbors+= [getTemperature(Coordinate(p.X, p.Y - 0.5, p.Z),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X, p.Y + 0.5, p.Z),indices, timestep, dataframe)]

    neighbors+= [getTemperature(Coordinate(p.X, p.Y, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X, p.Y, p.Z + 0.5),indices, timestep, dataframe)]

    ### distance - 2 degree
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y - 0.5, p.Z),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y + 0.5, p.Z),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y - 0.5, p.Z),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y + 0.5, p.Z),indices, timestep, dataframe)]

    neighbors+= [getTemperature(Coordinate(p.X, p.Y - 0.5, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X, p.Y + 0.5, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X, p.Y - 0.5, p.Z + 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X, p.Y + 0.5, p.Z + 0.5),indices, timestep, dataframe)]

    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y, p.Z + 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y, p.Z + 0.5),indices, timestep, dataframe)]

    ### diagonal neighbors distance - 3 degree
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y - 0.5, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y + 0.5, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y - 0.5, p.Z - 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y + 0.5, p.Z - 0.5),indices, timestep, dataframe)]

    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y - 0.5, p.Z + 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X - 0.5, p.Y + 0.5, p.Z + 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y - 0.5, p.Z + 0.5),indices, timestep, dataframe)]
    neighbors+= [getTemperature(Coordinate(p.X + 0.5, p.Y + 0.5, p.Z + 0.5),indices, timestep, dataframe)]

    return neighbors

def createDictionaries(dataframe):
    """
    It creates a dictionary with keys as (x,y,z) and temperature as value
    """
    start = time.time()
    dictionaryIndices,dictionaryValues = {},{}
    for i in range(len(dataframe)):
        (x,y,z) = dataframe.loc[i][:3].tolist()
        key = (x,y,z)
        if key!=(' ', ' ', ' '):
            value = dataframe.loc[i][3:].tolist()
            dictionaryIndices[key] = i
            dictionaryValues[key] = value
    stop = time.time()
    print('The time for dictionary creation is %2f seconds', (stop-start))
    return dictionaryIndices,dictionaryValues

In [4]:
def createDatabase(dataframe,timestep_Start,timestep_Stop,indices,toolpath):
    """
    It transforms the data into a database for each voxel at each time step
    """
    start = time.time()
    neighborColumns,historicalColumns,dictList = [],[],[]
    if timestep_Start<1:
        print("Timestep should start from greater than 0")
        return
    ## The temperature at this point for the past few timesteps
    for historical in range(5):
        historicalColumns += ['Tminus'+str(historical+1)]

    ## The temperature of neighboring 26 voxel elements
    for neighbor in range(26):
        neighborColumns += ['T'+str(neighbor+1)+'_t-1']

    columns = ['voxelLat','voxelLong','voxelVert','voxelType','timestep',\
    'x_voxel','y_voxel','z_voxel','layerNum','time_creation','time_elapsed',\
    'x_laser','y_laser','z_laser',\
    'x_distance','y_distance','z_distance','euclidean_distance_laser'] \
    + historicalColumns+ neighborColumns+['T_self']

    num_timesteps = len(dataframe.loc[0]-4)
    num_voxels = len(dataframe)
    


    for timestep in range(timestep_Start,timestep_Stop):#range(1,num_timesteps+1):
        for voxel in indices.keys():
            x,y,z = voxel

            voxelPosObject = Coordinate(x,y,z)
            T_self = getTemperature(voxelPosObject, indices, timestep, dataframe)
            if T_self == DEFAULT_TEMP:
                continue

            ##Extract the position of the laser
            x_laser,y_laser,z_laser = tuple(toolpath[timestep-1])

            ##Extract the absolute distance between the laser position and voxil position
            x_distance, y_distance, z_distance = abs(x-x_laser), abs(y-y_laser),abs(z-z_laser)

            ##Each layer is 0.5 so we can find number of layer by dividing height by 0.5
            layerNum = z/0.5

            laserPosObject = Coordinate(x_laser,y_laser,z_laser)

            distance_laser = voxelPosObject.distance(laserPosObject)

            dfIndex = indices[voxel]
            row = dataframe.loc[dfIndex].tolist()
            time_creation = float(row[3])
            time_current = float(timestep*0.1)
            time_elapsed = time_current - time_creation

            dictionary = {'voxelLat':'interior','voxelLong':'interior','voxelVert':'interior',
                        'timestep':timestep,
                        'x_voxel':x, 'y_voxel':y, 'z_voxel':z, 'layerNum':layerNum,
                         'time_creation':time_creation, 'time_elapsed':time_elapsed, 'x_laser':x_laser,'y_laser':y_laser,'z_laser':z_laser,
                         'x_distance':x_distance,'y_distance':y_distance,'z_distance':z_distance,
                          'euclidean_distance_laser':distance_laser}

            ##Extract the temperature of a voxel based on position and timestep
            for i in range(5):
                dictionary[historicalColumns[i]] = getTemperature(voxelPosObject, indices, timestep-i-1, dataframe)

            ##Extract the temperature of the neighboring temperatures
            neighborTemps = findNeighborTemperatures(voxelPosObject, indices, timestep-1, dataframe)

            for i in range(len(neighborTemps)):
                key = 'T'+str(i+1)+'_t-1'
                if neighborTemps[i] == DEFAULT_TEMP:
                    dictionary[key] = NON_EXISTING_TEMP

                    ##If the voxel left or right is missing
                    if i==0 or i==1:
                        dictionary['voxelLat'] = 'missing'

                    ##If the voxel longitudinally is missing
                    if i==3 or i==2:
                        dictionary['voxelLong'] = 'missing'

                    ##i==5 represents the voxel exactly above the voxel
                    ##It may be absent if it has not yet created
                    if i==5:
                        dictionary['voxelVert'] = 'missing'

                else:
                    dictionary[key] = neighborTemps[i]

            if dictionary['voxelVert'] == 'interior' \
            and dictionary['voxelLong'] == 'interior' \
            and dictionary['voxelLat'] == 'interior':
                dictionary['voxelType'] = 'interior'
            else:
                
                dictionary['voxelType'] = 'not interior'

            dictionary['T_self'] = T_self

            dictList += [dictionary]

    database =  pd.DataFrame(dictList,columns=columns)
    stop = time.time()
    print('Database creation took',stop-start,'seconds')

    return database

## Reading Database from the simulation and parsing the toolpath.

In [5]:
DIRECTORY = '../20-20-10-800'
df = pd.read_csv(DIRECTORY+'/'+'20-20-10-800'+'.csv',header=None).T
indices, _ = createDictionaries(df)
toolpath, _, _ = parse_toolpath(DIRECTORY ,'toolpath.crs',0.1) # 0.1 is the time interval of 0.1 seconds for each timestep. All voxels created in an interval of 0.1 seconds
# are considered to be created at the same timestep.

The time for dictionary creation is %2f seconds 18.07961106300354


In [5]:
df.head(60)

0    1    2       3    4        5        6        7        8        9     \
0   0.5  1.5  0.5       0  300  1876.72  1069.29  895.958  786.233  706.877   
1   0.5    1  0.5       0  300  1959.09  1068.08  896.858  787.094  707.581   
2     0  0.5  0.5       0  300   1643.9   1019.1  864.489  762.822  688.495   
3   0.5  0.5  0.5       0  300  1845.84  1067.81  897.931  788.166   708.43   
4     0    0  0.5       0  300  1554.23  1015.72  863.362  762.239  688.116   
5     0    1  0.5       0  300  1763.85  1020.86  863.354  761.559  687.467   
6     0  1.5  0.5       0  300  1746.63  1017.88   861.52  760.245  686.517   
7   0.5    0  0.5       0  300  1754.33  1065.69  897.344  787.972  708.326   
8     1  0.5  0.5  0.0077  300  2706.98  1209.53  991.543  859.221  764.371   
9     1    1  0.5  0.0077  300  2869.67  1210.24  991.075  858.672   763.91   
10    1  1.5  0.5  0.0154  300  2389.49  1208.86  990.055  857.832  763.234   
11    1    0  0.5  0.0154  300  2329.08  1207.45  990.962  858.908  764.134   
12  1.5    1  0.5  0.0231  300  3324.64  1368.69  1083.36   929.88  820.598   
13  1.5  0.5  0.5  0.0231  300  3303.29  1367.94  1083.54  930.132  820.835   
14  1.5    0  0.5  0.0308  300  3003.77  1363.92  1082.71  929.594   820.44   
15  1.5  1.5  0.5  0.0308  300  3026.39  1356.56  1082.38  929.119  819.992   
16    2  0.5  0.5  0.0462  300  3872.89  1637.32  1168.38  995.623  873.587   
17    2    1  0.5  0.0462  300  3876.13  1610.33  1168.44  995.504  873.439   
18    2    0  0.5  0.0538  300  3473.76  1572.55  1167.27  994.925  873.086   
19    2  1.5  0.5  0.0538  300  3478.99  1542.83  1167.02  994.719  872.826   
20  2.5  0.5  0.5  0.0615  300  3993.89  1827.65  1248.58  1054.88  921.681   
21  2.5    1  0.5  0.0615  300  3996.03  1799.35  1247.81  1054.82  921.557   
22  2.5    0  0.5  0.0692  300  3549.99  1746.19  1247.49  1054.07  921.107   
23  2.5  1.5  0.5  0.0692  300  3553.11  1770.93  1248.15  1053.98    920.9   
24    3  0.5  0.5  0.0846  300  3519.06  2024.27   1330.4  1108.55  965.241   
25    3    1  0.5  0.0846  300  3520.21  2032.02  1332.51  1108.49  965.116   
26    3  1.5  0.5  0.0923  300  2975.86  2005.54  1327.14  1107.61  964.397   
27    3    0  0.5  0.0923  300  2973.47  1988.31  1327.37  1107.57  964.606   
28  3.5    1  0.5     0.1  300  1614.58  2508.27  1432.27  1158.14  1004.89   
29  3.5  0.5  0.5     0.1  300  1614.62  2561.21  1421.06  1158.08  1005.04   
30  3.5  1.5  0.5  0.1077  300      300  2535.74  1420.23  1157.03   1004.1   
31  3.5    0  0.5  0.1077  300      300  2736.08  1410.88   1157.1  1004.36   
32    4    1  0.5  0.1231  300      300  3181.78  1573.58  1205.62  1041.99   
33    4  0.5  0.5  0.1231  300      300  3209.25  1603.19   1205.9  1042.21   
34    4    0  0.5  0.1308  300      300  3114.49  1491.08  1204.71  1041.48   
35    4  1.5  0.5  0.1308  300      300  3005.48  1555.68  1204.63  1041.11   
36  4.5  0.5  0.5  0.1385  300      300  3904.49  1711.92  1254.09  1077.88   
37  4.5    1  0.5  0.1385  300      300  3899.08  1709.65  1253.95  1077.58   
38  4.5  1.5  0.5  0.1462  300      300  3572.97  1633.77  1252.49  1076.62   
39  4.5    0  0.5  0.1462  300      300  3606.95  1610.16  1252.96  1077.11   
40    5    1  0.5  0.1615  300      300  4001.89  1756.28  1306.18   1112.7   
41    5  0.5  0.5  0.1615  300      300  3999.74  1824.11  1305.97  1113.04   
42    5  1.5  0.5  0.1692  300      300  3626.74  1713.92  1304.91  1111.66   
43    5    0  0.5  0.1692  300      300  3623.09  1768.34  1303.75  1112.18   
44  5.5    1  0.5  0.1769  300      300  3838.15  2062.03  1370.04  1148.04   
45  5.5  0.5  0.5  0.1769  300      300  3835.94  2166.56  1367.31  1148.39   
46  5.5    0  0.5  0.1846  300      300  3358.23  2083.76     1360  1147.35   
47  5.5  1.5  0.5  0.1846  300      300  3362.02  2085.78  1371.22  1147.03   
48    6    1  0.5     0.2  300      300  1714.05   2491.5   1483.6  1184.19   
49    6  0.5  0.5     0.2  300      300  1714.25  245

In [ ]:
cols = [0,1,2,3]
df_small = df[df.columns[cols]]
df_small.columns = ['x', 'y','z','time']
# df_small
# df_small

In [ ]:
df_new = df_small[df_small.z==10]
df_new.size

## Creating the database from timestep_start to timestep_stop
### Create database in batches of 100 or 200 timesteps
### All the created files can be merged in predict_cube and predict_cube_iterative notebooks

In [ ]:
db = createDatabase_Aggregated(df, 1,5,indices,toolpath)
saveNumpy(db.to_numpy(),'cubeAgg-20-20-10-800_1-3','../data_jagat/cube-20-20-10-800-processed')